In [21]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px

In [ ]:
df = pd.read_csv('/Users/Marcy_Student/Desktop/marcy/cleaned data.csv')
pd.set_option("display.float_format", "{:.2f}".format)
pd.set_option("display.expand_frame_repr", False)
pd.set_option("display.max_rows", 100)
df.head()
df.drop(['Unnamed: 0'],axis=1, inplace=True) # drop additionaal non needed column
df.keys()
df['mod_zcta']=df['mod_zcta'].astype(str)
df['date']=pd.to_datetime(df['date'])
df.dtypes # check data types

extract_date                  object
date                  datetime64[ns]
mod_zcta                      object
total_ed_visits                int64
ili_pne_visits                 int64
ili_pne_admissions             int64
dtype: object

In [41]:
# Group the data by zip code and date (mod_zcta)
df_zip_date = df.groupby(['date','mod_zcta'])[['ili_pne_visits','ili_pne_admissions','total_ed_visits']].sum().reset_index()

# visualise the repartition of the total Ed by zip code
fig= px.histogram(df_zip_date,x= 'mod_zcta', y='total_ed_visits',color= 'mod_zcta')
fig.show()

# takeaway, some zipcode are definitely more impacted, let's break it down with the flu,pneumonia disease/

In [42]:
#matching the zipcode to the borough name
zipcodes ={
'Manhattan': list(range(10001, 10282)),
'The Bronx': list(range(10451, 10475)),
'Brooklyn': list(range(11201, 11256)),
"Queens": list(range(11004, 11110)) + list(range(11351, 11698)),
'Staten Island': list(range(10301, 10314))}


In [43]:
# creating a function to apply to our new column
def my_borough(zipcode):
    try:
        zip_int= int(zipcode)
    except: 
        return None
    for borough, zip in zipcodes.items():
         if zip_int in zip:
            return borough
    return 'unknown'
        
df['borough']=df['mod_zcta'].apply(my_borough) # apply function to our original data set
df_zip_date['borough']=df_zip_date['mod_zcta'].apply(my_borough) # # apply function to our grouped data set
# added a column for the percentage admission rate in our grouped dataset
df_zip_date['admissions/visits']=df_zip_date['ili_pne_admissions']/df_zip_date['ili_pne_visits']*100

In [44]:
# some zip codes have 0 number of admissions for ili/pneu illness, so the percentange will be 0, droped them
df_zip_date['admissions/visits']=df_zip_date['admissions/visits'].fillna(0)

In [45]:
#check if the function for borough applied
df_zip_date[df_zip_date['mod_zcta']=='10002']

date mod_zcta  ili_pne_visits  ili_pne_admissions  total_ed_visits    borough  admissions/visits
1      2020-03-01    10002             425                  85             6545  Manhattan              20.00
178    2020-03-02    10002             595                  85             7395  Manhattan              14.29
352    2020-03-03    10002             595                  85             6970  Manhattan              14.29
529    2020-03-04    10002             425                   0             7820  Manhattan               0.00
706    2020-03-05    10002             425                  85             6800  Manhattan              20.00
...           ...      ...             ...                 ...              ...        ...                ...
151008 2022-07-10    10002             336                 168             5376  Manhattan              50.00
151183 2022-07-11    10002             252                   0             6048  Manhattan               0.00
151360 2022-07-12    10002             504                  84             6468  Manhattan              16.67
151536 2022-07-13    10002             588                  84             7728  Manhattan              14.29
151713 2022-07-14    10002             252                  84             7812  Manhattan              33.33

[866 rows x 7 columns]

In [46]:
# assigning Risks profile ( low moderate high risks )
def assign_risk(admission_rate):
    if admission_rate['ili_pne_visits'] < 120:# first quaartile of number of visit for ili/pne
        return "Low Volume _ Not Rated"
    elif admission_rate['admissions/visits']>50:
        return 'High risk'
    elif admission_rate['admissions/visits']>30:
        return 'Moderate risk'
    else :
        return 'Low risk'
df_zip_date['Risk_level']=df_zip_date.apply(assign_risk, axis=1) # created a column Risk level, useful if you need to know how severe is the admission rate for a specific zip code

In [58]:
top_5 = df_zip_date.nlargest(5,'admissions/visits') # top 5 zip code admission rate  
bottom_5= df_zip_date.nsmallest(5,'admissions/visits') # bottom 5 zip code admission rate  
df_top_bottom=pd.concat([top_5,bottom_5])  # top 5 and bottom 5 

fig= px.histogram(df_zip_date.head(100),x= 'mod_zcta', y='admissions/visits',color= 'mod_zcta',title='100 Admission rate accross zip code')
fig.show()

In [ ]:
print(df_zip_date['ili_pne_visits'].mean())
#to get more closer to the analysis, some admissions rate are higher because of a very small visit count, we will include only the zips with +100 visits for the same period(the average visit per period is 289 )
df_zip_date1 = df_zip_date[df_zip_date['ili_pne_visits']>= 100] #excluded zip code with very small amount of visits to avoid skewdness
# I created a filter for only the data where admissions rate for respiratory illness is greater to 50%, this targets zip codes with generally severe illess/flu
zip_rate_50 = df_zip_date1.loc[df_zip_date['admissions/visits']>50]

500.54248537921217


np.int64(177)

In [69]:
#zip_rate_50.sort_values(by='admissions/visits', ascending=True)
df_zip_date = df_zip_date[df_zip_date['ili_pne_admissions']>0]
#df_zip_date.sort_values(by='admissions/visits', ascending=True)

In [74]:
# let's calculate the average admission rate for the whole city and compare that to the average of the zips with over 50%
df_zip_date['admissions/visits'].mean() # 25,78
zip_rate_50['admissions/visits'].mean() # 76,34

np.float64(76.34122936654603)

In [76]:
# Now let's focuse on the the zip where admission rate is over 50%. the zip_rate_50
# Question: did thoses zip consistenly have high rates
fig1=px.histogram(zip_rate_50, x= 'date',y= 'admissions/visits', title='admission rate over time')
fig1.show()

In [ ]:
#df_zip_date['borough'].value_counts()
zip_rate_50['borough'].value_counts()
fig2 = px.histogram(zip_rate_50, x='borough', y='admissions/visits',color='borough') #repartition of the the zip_rate_50 by borough
fig2.show()